## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **African restaurant** in **Toronto**, Canada.

Since there are lots of restaurants in Toronto we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no African restaurants in vicinity**. We would also prefer locations **as close to the CN Tower as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. 

## Data <a name="data"></a>

based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to African restaurants in the neighborhood, if any

We decided to use a random location with a 25km radius from that location to select our neighbourhoods
Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of CN Tower will be obtained using **Foursquare Maps API geocoding** of address

In [380]:
!pip3 install geopy
!pip3 install folium
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
import random # library for random number generation

from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas import json_normalize

import folium # plotting library

print('Folium installed')
print('Libraries imported.')

Folium installed
Libraries imported.


## Define Foursquare Credentials and Version

### Neighborhood Candidates

#### Let's assume that the CN tower is our reference point. So let's start by converting the CN tower's address to its latitude and longitude coordinates. We will then get our location data from a 25km radius 

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>foursquare_agent</em>, as shown below.

In [381]:
CLIENT_ID = 'DVCKAH3PWXB0WWU04TYIKFEJYMCTUOUSWEFIBILUUMOTADTR' # your Foursquare ID
CLIENT_SECRET = 'DY0MEXS2DKQUKZXPGVH5FHO3Z30O4FVMTCCP5BQDBIQ5FLQZ' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: DVCKAH3PWXB0WWU04TYIKFEJYMCTUOUSWEFIBILUUMOTADTR
CLIENT_SECRET:DY0MEXS2DKQUKZXPGVH5FHO3Z30O4FVMTCCP5BQDBIQ5FLQZ


In [382]:
address = '301 Front Street West, Toronto, Ontario'

geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
CN_Tower = (latitude, longitude)
print(CN_Tower)


(43.6425637, -79.38708718320467)


In [383]:
search_query = 'African'
radius = 25000
print(search_query + ' .... OK!')

African .... OK!


In [384]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=DVCKAH3PWXB0WWU04TYIKFEJYMCTUOUSWEFIBILUUMOTADTR&client_secret=DY0MEXS2DKQUKZXPGVH5FHO3Z30O4FVMTCCP5BQDBIQ5FLQZ&ll=43.6425637,-79.38708718320467&v=20180604&query=African&radius=25000&limit=30'

In [385]:
results = requests.get(url).json()
results

r Memorial',
    'location': {'address': 'Queen St W',
     'crossStreet': 'University Ave',
     'lat': 43.650900163583934,
     'lng': -79.38617571756487,
     'labeledLatLngs': [{'label': 'display',
       'lat': 43.650900163583934,
       'lng': -79.38617571756487}],
     'distance': 930,
     'cc': 'CA',
     'city': 'Toronto',
     'state': 'ON',
     'country': 'Canada',
     'formattedAddress': ['Queen St W (University Ave)',
      'Toronto ON',
      'Canada']},
    'categories': [{'id': '4bf58dd8d48988d166941735',
      'name': 'Sculpture Garden',
      'pluralName': 'Sculpture Gardens',
      'shortName': 'Sculpture',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/sculpture_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1587574464',
    'hasPerk': False},
   {'id': '4ba5940cf964a520da1339e3',
    'name': 'African Palace',
    'location': {'address': '977 Bloor St. W',
     'crossStreet': 'at Dovercourt Rd.',
     '

In [386]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
df = json_normalize(venues)
df.head()

id                          name  \
0  4c4645f5f88dc928a154af75    South African War Memorial   
1  4ba5940cf964a520da1339e3                African Palace   
2  54ee1726498e496154bf9103  Kal & Mooy East African Food   
3  4e1ef0cd814d82553443d8c3               African Village   
4  541b3a0c498ea1eb4f13f069         Tree Top African Cafe   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d166941735', 'name': 'S...  v-1587574464    False   
1  [{'id': '4bf58dd8d48988d1c8941735', 'name': 'A...  v-1587574464    False   
2  [{'id': '4bf58dd8d48988d1c8941735', 'name': 'A...  v-1587574464    False   
3  [{'id': '4bf58dd8d48988d10a941735', 'name': 'E...  v-1587574464    False   
4  [{'id': '4bf58dd8d48988d1c8941735', 'name': 'A...  v-1587574464    False   

     location.address location.crossStreet  location.lat  location.lng  \
0          Queen St W       University Ave     43.650900    -79.386176   
1     977 Bloor St. W    at Dovercourt Rd.     43.661160    -79.429040   
2      238 Queen St W                  NaN     43.650020    -79.390574   
3      368 Queen St E           Parliament     43.655888    -79.363990   
4  620 Dundas St West          Denison Ave     43.652137    -79.402169   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 43.65090016358393...                930   
1  [{'label': 'display', 'lat': 43.66116, 'lng': ...               3962   
2  [{'label': 'display', 'lat': 43.6500203103337,...                876   
3  [{'label': 'display', 'lat': 43.65588781419645...               2379   
4  [{'label': 'display', 'lat': 43.65213690654421...               1615   

  location.cc location.city location.state location.country  \
0          CA       Toronto             ON           Canada   
1          CA       Toronto             ON           Canada   
2          CA       Toronto             ON           Canada   
3          CA       Toronto             ON           Canada   
4          CA       Toronto             ON           Canada   

                           location.formattedAddress location.postalCode  \
0  [Queen St W (University Ave), Toronto ON, Canada]                 NaN   
1  [977 Bloor St. W (at Dovercourt Rd.), Toronto ...             M6H 1L8   
2       [238 Queen St W, Toronto ON M5V 1Z7, Canada]             M5V 1Z7   
3  [368 Queen St E (Parliament), Toronto ON, Canada]                 NaN   
4  [620 Dundas St West (Denison Ave), Toronto ON,...                 NaN   

  location.neighborhood  
0                   NaN  
1                   NaN  
2                   NaN  
3                   NaN  
4                   NaN

In [387]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in df.columns if col.startswith('location.')] + ['id']
df_fd = df.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
df_fd['categories'] = df_fd.apply(get_category_type, axis=1)

# clean column names by keeping only last term
df_fd.columns = [column.split('.')[-1] for column in df_fd.columns]

df_fd

name  \
0                          South African War Memorial   
1                                      African Palace   
2                        Kal & Mooy East African Food   
3                                     African Village   
4                               Tree Top African Cafe   
5                         Kiondo African Imports Inc.   
6                          African Delight ( somali )   
7   African Canadian Social Development Council (A...   
8      The Empire: Middle Eastern & East African Food   
9                          African Players Restaurant   
10                    Mr. Sety - African Spiritualist   
11              Grant Avenue African Methodist Chruch   
12                                South African Store   
13                                African Lion Safari   
14                    South African Consulate General   
15                               Mosaic African store   
16                          Naomi African Food Market   
17                                   African Penguins   
18                                    African Savanna   
19                                    Vision Africana   
20                             African Lion Safari II   
21                        African Rainforest Pavilion   
22          Reptilia African Rock Python Feeding Time   
23                                      Atwima Market   

                     categories                        address  \
0              Sculpture Garden                     Queen St W   
1            African Restaurant                977 Bloor St. W   
2            African Restaurant                 238 Queen St W   
3          Ethiopian Restaurant                 368 Queen St E   
4            African Restaurant             620 Dundas St West   
5           Arts & Crafts Store          323 Queen Street East   
6            African Restaurant                            NaN   
7                    Non-Profit  2238 Dundas St. W. Suite 107b   
8     Middle Eastern Restaurant         1018 Bloor Street West   
9                           Bar                            NaN   
10              Doctor's Office                            NaN   
11                       Church       2929 Gerrard Street East   
12                       Market               3889 Bathurst St   
13         Other Great Outdoors                            NaN   
14          Embassy / Consulate       110 Sheppard Avenue East   
15                         None      Jane and Eddystone avenue   
16                       Market                 3226 Weston Rd   
17                  Zoo Exhibit                            NaN   
18                  Zoo Exhibit                            NaN   
19                     Building       1760 St. Clair Ave. West   
20  Professional & Other Places                            NaN   
21                  Zoo Exhibit                            NaN   
22                  Zoo Exhibit                            NaN   
23                       Market            287 Morningside Ave   

          crossStreet        lat        lng  \
0      University Ave  43.650900 -79.386176   
1   at Dovercourt Rd.  43.661160 -79.429040   
2                 NaN  43.650020 -79.390574   
3          Parliament  43.655888 -79.363990   
4         Denison Ave  43.652137 -79.402169   
5                 NaN  43.655158 -79.365814   
6                 NaN  43.659503 -79.437403   
7                 NaN  43.654366 -79.451795   
8           Salem Av.  43.660855 -79.430906   
9                 NaN  43.689563 -79.495715   
10                NaN  43.700179 -79.415874   
11       Golfview Ave  43.681751 -79.310314   
12       Edinburgh Dr  43.742272 -79.435316   
13                NaN  43.602032 -79.623741   
14                NaN  43.765484 -79.394310   
15                NaN  43.741347 -79.527365   
16       Bradstock Rd  43.738630 -79.539876   
17                NaN  43.819492 -79.185969   
18                NaN  43.819115 -79.184692   
19                NaN  43.674154

In [388]:
missing_data = df_fd.isnull()
missing_data.head(5)

name  categories  address  crossStreet    lat    lng  labeledLatLngs  \
0  False       False    False        False  False  False           False   
1  False       False    False        False  False  False           False   
2  False       False    False         True  False  False           False   
3  False       False    False        False  False  False           False   
4  False       False    False        False  False  False           False   

   distance     cc   city  state  country  formattedAddress  postalCode  \
0     False  False  False  False    False             False        True   
1     False  False  False  False    False             False       False   
2     False  False  False  False    False             False       False   
3     False  False  False  False    False             False        True   
4     False  False  False  False    False             False        True   

   neighborhood     id  
0          True  False  
1          True  False  
2          True  False  
3          True  False  
4          True  False

In [389]:
for column in missing_data.columns.values.tolist():
    print(column)
    print (missing_data[column].value_counts())
    print("") 

name
False    24
Name: name, dtype: int64

categories
False    23
True      1
Name: categories, dtype: int64

address
False    15
True      9
Name: address, dtype: int64

crossStreet
True     15
False     9
Name: crossStreet, dtype: int64

lat
False    24
Name: lat, dtype: int64

lng
False    24
Name: lng, dtype: int64

labeledLatLngs
False    24
Name: labeledLatLngs, dtype: int64

distance
False    24
Name: distance, dtype: int64

cc
False    24
Name: cc, dtype: int64

city
False    19
True      5
Name: city, dtype: int64

state
False    20
True      4
Name: state, dtype: int64

country
False    24
Name: country, dtype: int64

formattedAddress
False    24
Name: formattedAddress, dtype: int64

postalCode
True     13
False    11
Name: postalCode, dtype: int64

neighborhood
True     23
False     1
Name: neighborhood, dtype: int64

id
False    24
Name: id, dtype: int64



In [390]:
df_fd.dropna(subset=['address'], axis=0, inplace=True)
df_fd.head(25)

name  \
0                          South African War Memorial   
1                                      African Palace   
2                        Kal & Mooy East African Food   
3                                     African Village   
4                               Tree Top African Cafe   
5                         Kiondo African Imports Inc.   
7   African Canadian Social Development Council (A...   
8      The Empire: Middle Eastern & East African Food   
11              Grant Avenue African Methodist Chruch   
12                                South African Store   
14                    South African Consulate General   
15                               Mosaic African store   
16                          Naomi African Food Market   
19                                    Vision Africana   
23                                      Atwima Market   

                   categories                        address  \
0            Sculpture Garden                     Queen St W   
1          African Restaurant                977 Bloor St. W   
2          African Restaurant                 238 Queen St W   
3        Ethiopian Restaurant                 368 Queen St E   
4          African Restaurant             620 Dundas St West   
5         Arts & Crafts Store          323 Queen Street East   
7                  Non-Profit  2238 Dundas St. W. Suite 107b   
8   Middle Eastern Restaurant         1018 Bloor Street West   
11                     Church       2929 Gerrard Street East   
12                     Market               3889 Bathurst St   
14        Embassy / Consulate       110 Sheppard Avenue East   
15                       None      Jane and Eddystone avenue   
16                     Market                 3226 Weston Rd   
19                   Building       1760 St. Clair Ave. West   
23                     Market            287 Morningside Ave   

          crossStreet        lat        lng  \
0      University Ave  43.650900 -79.386176   
1   at Dovercourt Rd.  43.661160 -79.429040   
2                 NaN  43.650020 -79.390574   
3          Parliament  43.655888 -79.363990   
4         Denison Ave  43.652137 -79.402169   
5                 NaN  43.655158 -79.365814   
7                 NaN  43.654366 -79.451795   
8           Salem Av.  43.660855 -79.430906   
11       Golfview Ave  43.681751 -79.310314   
12       Edinburgh Dr  43.742272 -79.435316   
14                NaN  43.765484 -79.394310   
15                NaN  43.741347 -79.527365   
16       Bradstock Rd  43.738630 -79.539876   
19                NaN  43.674154 -79.461102   
23        Kingston Rd  43.770977 -79.184809   

                                       labeledLatLngs  distance  cc  \
0   [{'label': 'display', 'lat': 43.65090016358393...       930  CA   
1   [{'label': 'display', 'lat': 43.66116, 'lng': ...      3962  CA   
2   [{'label': 'display', 'lat': 43.6500203103337,...       876  CA   
3   [{'label': 'display', 'lat': 43.65588781419645...      2379  CA   
4   [{'label': 'display', 'lat': 43.65213690654421...      1615  CA   
5   [{'label': 'display', 'lat': 43.65515815351774...      2214  CA   
7   [{'label': 'display', 'lat': 43.6543663840279,...      5375  CA   
8   [{'label': 'display', 'lat': 43.66085492889121...      4074  CA   
11  [{'label': 'display', 'lat': 43.68175116678484...      7566  CA   
12  [{'label': 'display', 'lat': 43.742272, 'lng':...     11758  CA   
14  [{'label': 'display', 'lat': 43.76548444248979...     13695  CA   
15  [{'label': 'display', 'lat': 43.74134670858788...     15760  CA   
16  [{'label': 'display', 'lat': 43.7386300073063,...     16297  CA   
19  [{'label': 'display', 'lat': 43.674154, 'lng':...      6920  CA   
23  [{'label': 'display', 'lat': 43.770977, 'lng':...     21663  CA   

           city state country  \
0       Toronto    ON  Canada   
1       Toronto    ON  Canada   
2       Toronto    ON  Canada   
3       Toronto    ON  Canada   
4       Toronto    ON  Canada   
5       Toronto    ON  

In [391]:
indexNames = df_fd[ (df_fd['categories'] != "African Restaurant") & (df_fd['categories'] != "Ethiopian Restaurant") & (df_fd['categories'] != "Middle Eastern Restaurant") ].index
df_fd.drop(indexNames , inplace=True)
df_fd.head(15)

name                 categories  \
1                                  African Palace         African Restaurant   
2                    Kal & Mooy East African Food         African Restaurant   
3                                 African Village       Ethiopian Restaurant   
4                           Tree Top African Cafe         African Restaurant   
8  The Empire: Middle Eastern & East African Food  Middle Eastern Restaurant   

                  address        crossStreet        lat        lng  \
1         977 Bloor St. W  at Dovercourt Rd.  43.661160 -79.429040   
2          238 Queen St W                NaN  43.650020 -79.390574   
3          368 Queen St E         Parliament  43.655888 -79.363990   
4      620 Dundas St West        Denison Ave  43.652137 -79.402169   
8  1018 Bloor Street West          Salem Av.  43.660855 -79.430906   

                                      labeledLatLngs  distance  cc     city  \
1  [{'label': 'display', 'lat': 43.66116, 'lng': ...      3962  CA  Toronto   
2  [{'label': 'display', 'lat': 43.6500203103337,...       876  CA  Toronto   
3  [{'label': 'display', 'lat': 43.65588781419645...      2379  CA  Toronto   
4  [{'label': 'display', 'lat': 43.65213690654421...      1615  CA  Toronto   
8  [{'label': 'display', 'lat': 43.66085492889121...      4074  CA  Toronto   

  state country                                   formattedAddress postalCode  \
1    ON  Canada  [977 Bloor St. W (at Dovercourt Rd.), Toronto ...    M6H 1L8   
2    ON  Canada       [238 Queen St W, Toronto ON M5V 1Z7, Canada]    M5V 1Z7   
3    ON  Canada  [368 Queen St E (Parliament), Toronto ON, Canada]        NaN   
4    ON  Canada  [620 Dundas St West (Denison Ave), Toronto ON,...        NaN   
8    ON  Canada  [1018 Bloor Street West (Salem Av.), Toronto O...        NaN   

  neighborhood                        id  
1          NaN  4ba5940cf964a520da1339e3  
2          NaN  54ee1726498e496154bf9103  
3          NaN  4e1ef0cd814d82553443d8c3  
4          NaN  541b3a0c498ea1eb4f13f069  
8          NaN  4b7b4021f964a5208d5a2fe3

In [392]:
df_fd.drop(['name', 'categories', 'crossStreet', 'labeledLatLngs', 'distance','postalCode','cc','city','state','country','formattedAddress','neighborhood','id'], axis=1, inplace=True)
df_fd.head()

address        lat        lng
1         977 Bloor St. W  43.661160 -79.429040
2          238 Queen St W  43.650020 -79.390574
3          368 Queen St E  43.655888 -79.363990
4      620 Dundas St West  43.652137 -79.402169
8  1018 Bloor Street West  43.660855 -79.430906

In [600]:
df_fd.reset_index()
df_fd = df_fd.reindex(index=range(0,5))
df_fd.head()

address        lat        lng  Restaurants in area
0         977 Bloor St. W  43.661160 -79.429040                  0.0
1          238 Queen St W  43.650020 -79.390574                  0.0
2          368 Queen St E  43.655888 -79.363990                  0.0
3      620 Dundas St West  43.652137 -79.402169                  0.0
4  1018 Bloor Street West  43.660855 -79.430906                  0.0

In [394]:
#save into local file
df_fd.to_pickle('./locations.pkl') 

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.


In [395]:
# Category IDs corresponding to African restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

African_restaurant_categories = ['4bf58dd8d48988d1c8941735','4bf58dd8d48988d10a941735']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Canada', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [396]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found African restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    African_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, CLIENT_ID, CLIENT_SECRET, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_African = is_restaurant(venue_categories, specific_filter=African_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_African, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_African:
                    African_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, African_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
italian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('African_restaurants_350.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, African_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(African_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [397]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of African restaurants:', len(African_restaurants))
print('Percentage of African restaurants: {:.2f}%'.format(len(African_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 1116
Total number of African restaurants: 10
Percentage of African restaurants: 0.90%
Average number of restaurants in neighborhood: 4.906593406593407


In [ ]:
data = {'':  ['African', 'Non-African',], 'Total number of restaurants': [10,1116], 'Percentage of Restaurants': [0.896,]}

df = pd.DataFrame (data, columns = ['First Column Name','Second Column Name',...])

In [398]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4f6d1982e4b062083139cc8a', 'Village of Thai Peterborough', 43.654336, -79.339295, 'Peterborough', 46, False, -5310958.995644974, 10502366.095392086)
('539a1eff498e1bf8518e4eb5', 'Food Dudes Pantry', 43.65630014845779, -79.3382027627999, '24 Carlaw Ave (at Lake Shore Blvd E), Toronto ON M4M 2R7', 280, False, -5310660.2536905715, 10502205.67661057)
('4bc1df994cdfc9b6a3229521', "Gale's Snack Bar", 43.658239, -79.339077, '539 Eastern Ave (Carlaw Ave), Toronto ON', 93, False, -5310340.672131852, 10502272.900043106)
('519d414a498e6cc21f677ff4', 'Tabule', 43.65973096534363, -79.3463408134466, '810 Queen St East, Toronto ON M4M 1H7', 264, False, -5310011.3152562445, 10503086.021006016)
('5ba55b9ae0c0c9002c29d056', 'EAT BKK Thai Kitchen', 43.66045, -79.343113, '898 Queen St E (Logan Ave), Toronto ON M4M 1J3', 318, False, -5309937.784912162, 10502700.609016394)
('53c4629f498ef9114ca25be3', 'braised', 43.660451867292366, -79.34334606916272, '896 Q

In [399]:
print('List of African restaurants')
print('---------------------------')
for r in list(African_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(African_restaurants))

List of African restaurants
---------------------------
('596e3fd92f97ec370ba90afb', 'King Solomon Queen Of Sheba', 43.655731, -79.363986, '360 Queen St E, Toronto ON M5A 1T1', 209, True, -5310423.742987487, 10505194.372815857)
('5a91b595b1538e70dc66f385', 'Enat Buna', 43.65392, -79.37157, '175 Queen Street East (Queen and George), Toronto ON M5A 1S2', 346, True, -5310615.322206728, 10506102.29425736)
('4c4e2474f53d0f47f18b13a6', 'Ethiopiques', 43.65651274304155, -79.377077748846, '227 Church St. (at Dundas St. E), Toronto ON M5B 1Y7', 251, True, -5310132.554085254, 10506693.023237238)
('4a72360ef964a52098da1fe3', 'Ethiopian House', 43.6665987043968, -79.38566906742606, '4 Irwin Ave. (at Yonge St), Toronto ON', 278, True, -5308418.31105637, 10507507.873198124)
('4c913d621adc3704635d2ed1', 'Abyssinia', 43.66333916029408, -79.41853523254395, '735 Bloor St. W. (at Grace St.), Toronto ON M6G 1L5', 268, True, -5308515.238756643, 10511360.536199361)
('4b4960fdf964a520ba6e26e3', 'Pero Restaur

In [400]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 125):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: 
Restaurants around location 102: 
Restaurants around location 103: 
Restaurants around location 104: 
Restaurants around location 105: The Hub
Restaurants around location 106: 
Restaurants around location 107: Market Street Catch, Buster's Sea Cove, Paddington's Pump, European Delight, True True Diner, Bombay Palace, St. Lawrence Pizza and Pasta, Ardo
Restaurants around location 108: Mystic Muffin, The George Street Diner, Fusaro's, Schnitzel Queen, GEORGE Restaurant, Ueno Sushi Deli Cafe, Olympos / crow-bar
Restaurants around location 109: King's Place647-352-0786, Citrus, Casey's Outdoor Patio
Restaurants around location 110: King's Place647-352-0786, retsina, Kabab & Tikah House
Restaurants around location 111: Zakkushi ざっ串, Chew Chew's Diner, Kabab & Tikah House
Restaurants around location 112: Mr. Jerk, Cranberries, Cabbage Town Kitchen, Tender Trap Restaurant, El Charro
Restaurants around lo

Let's now see all the collected restaurants in our area of interest on map, and let's also show African restaurants in different color.

In [595]:
map_Toronto = folium.Map(location=CN_Tower, zoom_start=12.5)
folium.Marker(CN_Tower, popup='CN Tower').add_to(map_Toronto)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_Toronto)
map_Toronto #CN_Tower

Looking good. So now we have all the restaurants in area within few kilometers from Alexanderplatz, and we know which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Berlin that have low restaurant density, particularly those with low number of Italian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required data: location and type (category) of every restaurant within 6km from Berlin center (Alexanderplatz). We have also identified Italian restaurants (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of 'restaurant density' across different areas of Berlin - we will use heatmaps to identify a few promising areas close to center with low number of restaurants in general (and no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create clusters of locations that meet some basic requirements established in discussion with stakeholders: we will take into consideration locations with no more than two restaurants in radius of 250 meters, and we want locations without Italian restaurants in radius of 400 meters. We will present map of all such locations but also create clusters (using k-means clustering) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [419]:
location_restaurants_count = np.array([len(r) for r in location_restaurants])

#df_fd['Restaurants in area'] = location_restaurants_count
#print(location_restaurants_count)
print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())
df_df=pd.DataFrame(location_restaurants_count , columns=['Restaurants in area'])
print(df_df)

Average number of restaurants in every area with radius=300m: 4.906593406593407
     Restaurants in area
0                      0
1                      0
2                      0
3                      0
4                      0
..                   ...
359                    1
360                   14
361                   13
362                    0
363                    6

[364 rows x 1 columns]


In [509]:
df_fd = df_fd.append(df_df, ignore_index = True)
df_fd.shape

(1097, 4)

In [429]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

African_latlons = [[res[2], res[3]] for res in African_restaurants.values()]

In [511]:
values = {'address': 0, 'lat': 0, 'lng': 0, 'Restaurants in area': 0}
df_fd = df_fd.fillna(value=values)
df_fd = df_fd.drop(df_fd.index[5:1097])
df_fd.head()

address        lat        lng  Restaurants in area
0         977 Bloor St. W  43.661160 -79.429040                  0.0
1          238 Queen St W  43.650020 -79.390574                  0.0
2          368 Queen St E  43.655888 -79.363990                  0.0
3      620 Dundas St West  43.652137 -79.402169                  0.0
4  1018 Bloor Street West  43.660855 -79.430906                  0.0

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show a few circles indicating distance of 1km, 2km and 3km from CN Tower.

In [512]:
from folium import plugins
from folium.plugins import HeatMap

map_Toronto = folium.Map(location=CN_Tower, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_Toronto) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_Toronto)
folium.Marker(CN_Tower).add_to(map_Toronto)
folium.Circle(CN_Tower, radius=1000, fill=False, color='white').add_to(map_Toronto)
folium.Circle(CN_Tower, radius=2000, fill=False, color='white').add_to(map_Toronto)
folium.Circle(CN_Tower, radius=3000, fill=False, color='white').add_to(map_Toronto)
map_Toronto

Looks like a few pockets of low restaurant density closest to the CN Tower can be found west, north-west and east from it.

Let's create another heatmap map showing heatmap/density of African restaurants only.

In [434]:
map_Toronto = folium.Map(location=CN_Tower, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_Toronto) #cartodbpositron cartodbdark_matter
HeatMap(African_latlons).add_to(map_Toronto)
folium.Marker(CN_Tower).add_to(map_Toronto)
folium.Circle(CN_Tower, radius=1000, fill=False, color='white').add_to(map_Toronto)
folium.Circle(CN_Tower, radius=2000, fill=False, color='white').add_to(map_Toronto)
folium.Circle(CN_Tower, radius=3000, fill=False, color='white').add_to(map_Toronto)
map_Toronto

In [466]:
roi_x_min = CN_Tower_x + 2000
roi_y_max = CN_Tower_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 800
roi_center_y = roi_y_max + 1000
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_Toronto = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_Toronto)
folium.Marker(CN_Tower).add_to(map_Toronto)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_Toronto)
map_Toronto

Not bad - this nicely covers all the pockets of low restaurant density in Toronto closest to the CN Tower.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [468]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

1597 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: number of restaurants in vicinity (we'll use radius of 250 meters) and distance to closest **African** restaurant.

In [541]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_African_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, African_restaurants)
    roi_African_distances.append(distance)
print('done.')


Generating data on location candidates...done.


In [558]:
# Let's put this into dataframe
df_roi = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to African restaurant':roi_African_distances})
df_roi.head(10)


Latitude  Longitude             X             Y  Restaurants nearby  \
0  43.659982 -79.385415 -5.309474e+06  1.050760e+07                   4   
1  43.660603 -79.385510 -5.309374e+06  1.050760e+07                   4   
2  43.656507 -79.385635 -5.310024e+06  1.050768e+07                  11   
3  43.657128 -79.385730 -5.309924e+06  1.050768e+07                   5   
4  43.657749 -79.385824 -5.309824e+06  1.050768e+07                   5   
5  43.658370 -79.385919 -5.309724e+06  1.050768e+07                   3   
6  43.658991 -79.386014 -5.309624e+06  1.050768e+07                   2   
7  43.659612 -79.386108 -5.309524e+06  1.050768e+07                   4   
8  43.660233 -79.386203 -5.309424e+06  1.050768e+07                   6   
9  43.660853 -79.386298 -5.309324e+06  1.050768e+07                   4   

   Distance to African restaurant  
0                     1059.488494  
1                      959.862520  
2                      994.509803  
3                     1010.306162  
4                     1035.561362  
5                     1069.605595  
6                     1111.631649  
7                     1119.463503  
8                     1020.793183  
9                      922.409296

OK. Let us now **filter** those locations: we're interested only in **locations with no more than five restaurants in radius of 250 meters**, and **no African restaurants in radius of 600 meters**.

In [559]:
good_res_count = np.array((df_roi['Restaurants nearby']<=5))
print('Locations with no more than five restaurants nearby:', good_res_count.sum())

good_Afr_distance = np.array((df_roi['Distance to African restaurant']>=600))
print('Locations with no African restaurants within 600m:', good_Afr_distance.sum())

good_locations = np.logical_and(good_res_count, good_Afr_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi[good_locations]

Locations with no more than five restaurants nearby: 1203
Locations with no African restaurants within 600m: 1355
Locations with both conditions met: 1027


On a map

In [560]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_Toronto = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_Toronto)
HeatMap(restaurant_latlons).add_to(map_Toronto)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_Toronto)
folium.Marker(CN_Tower).add_to(map_Toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Toronto) 
map_Toronto

Looking good. We now have a bunch of locations fairly close to the CN Tower and we know that each of those locations has no more than five restaurants in radius of 250m, and no African restaurant closer than 600m. Any of those locations is a potential candidate for a new African restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [561]:
map_Toronto = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_Toronto)
folium.Marker(CN_Tower).add_to(map_Toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Toronto)
map_Toronto

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* African restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [562]:
!pip3 install sklearn
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_Toronto = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_Toronto)
HeatMap(restaurant_latlons).add_to(map_Toronto)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_Toronto)
folium.Marker(CN_Tower).add_to(map_Toronto)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_Toronto) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Toronto)
map_Toronto

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [592]:
map_Toronto = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(CN_Tower).add_to(map_Toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_Toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Toronto)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_Toronto) 
map_Toronto

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [591]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(lat, lon) 
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, CN_Tower_x, CN_Tower_y)
    print('{}{} => {:.1f}km from CN Tower'.format(addr, ' '*(50-len(addr)), d/1000))

    


Addresses of centers of areas recommended for further analysis

161, St George Street, The Annex, University—Rosedale, Old Toronto, Toronto, Golden Horseshoe, Ontario, M5R 2N5, Canada => 4.7km from CN Tower
17, Jersey Avenue, Little Italy, University—Rosedale, Old Toronto, Toronto, Golden Horseshoe, Ontario, M6G 2V7, Canada => 4.2km from CN Tower
University of Toronto, University Avenue, Discovery District, University—Rosedale, Old Toronto, Toronto, Golden Horseshoe, Ontario, M5G 2C4, Canada => 2.9km from CN Tower
193, Christie Street, Christie Pits, University—Rosedale, Old Toronto, Toronto, Golden Horseshoe, Ontario, M6G 3B9, Canada => 5.7km from CN Tower
105, Major Street, Kensington Market, University—Rosedale, Old Toronto, Toronto, Golden Horseshoe, Ontario, M5T 1S3, Canada => 3.4km from CN Tower
Dewson Street Junior Public School, 65, Concord Avenue, Dufferin Grove, Davenport, Old Toronto, Toronto, Golden Horseshoe, Ontario, M6H 2N9, Canada => 4.9km from CN Tower
University of To

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no African restaurants nearby, all zones being fairly central with all less than 6km from CN Tower. Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located around the University of Toronto which is interesting due to being popular with international students, fairly close to the CN Tower and well connected by public transport.

In [593]:
map_Toronto = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(CN_Tower, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_Toronto)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_Toronto) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_Toronto)
map_Toronto

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Toronto there are pockets of low restaurant density fairly close to centre of the city. Lowest concentration of restaurants was detected west, north-west and east from the CN Tower, so we focused our attention there.

Although zones are shown on map with a radius of 500 meters, their shape is actually very irregular and their centres or addresses should be considered only as a starting point for exploring area neighbourhoods in search for potential restaurant locations. A lot of the zones are located around the University of Toronto which is interesting due to it being popular with international students, fairly close to the CN Tower and well connected by public transport.

## Conclusion <a name="conclusion"></a>

The final decision on an optimal restaurant location will be made by stakeholders based on specific characteristics of neighbourhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location, noise levels and prices.

In the end we were able to cook up some suggestions from our model. This is the magic of data science.